In [42]:
import numpy as np
import xarray as xr
import pandas as pd
import matplotlib as mpl
import matplotlib.pyplot as plt
import shutil
from shutil import copyfile


In [43]:
def check_mask_nearby(i,j,mask,ndist):
    # i = index along i of point to test
    # j = index along j of point to test
    # mask = 2D mask 
    # ndist = distance from center to check
    if (i > (ndist-1)):
        TEST_i = np.nansum(mask[i-ndist:i+ndist+1,j])
    else:
        TEST_i = np.nansum(mask[i:i+ndist+1,j])
    if (j > (ndist-1)):
        TEST_j = np.nansum(mask[i,j-ndist:j+ndist+1])
    else:
        TEST_j = np.nansum(mask[i,j:j+ndist+1])
    return TEST_i, TEST_j    


In [44]:
def find_nearest_sea_point(i,j,mask,ndist,rnf_data):
        arr= np.array([rnf_data[i-ndist,j] + mask[i-ndist,j], \
                    rnf_data[i+ndist,j]    + mask[i+ndist,j],    \
                    rnf_data[i,j-ndist]   + mask[i,j-ndist],   \
                    rnf_data[i,j+ndist]   + mask[i,j+ndist]])
        ind=np.array(np.argwhere(arr==0))
        if len(ind)==1:
            if ind == 0:
                return(i-ndist,j)
            if ind == 1:
                return(i+ndist,j)  
            if ind == 2:
                return(i,j-ndist)      
            if ind == 3:
                return(i,j+ndist)
            return ind
        elif len(ind)>1: # more than one unused sea point around
#             print("problem",len(ind) )
            out=[]
            if arr[0] == 0:
                out=np.append(out,[i-ndist,j])
            if arr[1] == 0:
                out=np.append(out,[i+ndist,j])  
            if arr[2] == 0:
                out=np.append(out,[i,j-ndist])      
            if arr[3] == 0:
                out=np.append(out,[i,j+ndist])
            return out
        else: # Worst case : there is no unused sea point around : return used sea point around
            print("WARNING : point at i,j =",i,j, " has no empty sea point around. Adding rnf value to the nearby sea points")
            out=[]
            if arr[0] < 1:
                out=np.append(out,[i-ndist,j])
            if arr[1] < 1:
                out=np.append(out,[i+ndist,j])  
            if arr[2] < 1:
                out=np.append(out,[i,j-ndist])      
            if arr[3] < 1:
                out=np.append(out,[i,j+ndist])
            return out

In [45]:
def get_npoints(i,j,mask,ndist,rnf_data):
        # return the number of sea points at ndist distance
        arr= np.array([rnf_data[i-ndist,j] + mask[i-ndist,j], \
                    rnf_data[i+ndist,j]    + mask[i+ndist,j],    \
                    rnf_data[i,j-ndist]   + mask[i,j-ndist],   \
                    rnf_data[i,j+ndist]   + mask[i,j+ndist]])
        ind=np.array(np.argwhere(arr==0))
        if len(ind>0):
            return len(ind)
        else:
            ind=np.array(np.argwhere(arr<1))
            return len(ind)



In [46]:
def find_nearest_coast_point(i,j,mask,rnf_data,nseuil):
    out=[]
    n=1
    var=0
    nip1,nim1,njp1,njm1 = 0 ,0 ,0 ,0 
    while (var==0) and (n<nseuil):
        if mask[i+n,j]==1:
            if (rnf_data[i+n-1,j] == 0.):
                if (mask[i+n-1,j] == 0.):
                    out=np.append(out,[i+n-1,j])
                else:
                    nip1=1
        if mask[i-n,j]==1:
            if (rnf_data[i-n+1,j] == 0.): 
                if (mask[i-n+1,j] == 0.):
                    out=np.append(out,[i-n+1,j])
                else:
                    nim1=1
        if mask[i,j+n]==1:
            if (rnf_data[i,j+n-1] == 0.):
                if (mask[i,j+n-1] == 0.):
                    out=np.append(out,[i,j+n-1])
                else:
                    njp1=1
        if mask[i,j-n]==1:
            if (rnf_data[i,j-n+1] == 0.): 
                if (mask[i,j-n+1] == 0.):
                    out=np.append(out,[i,j-n+1])  
                else:
                    njm1=1
           
        var=len(out)
        if var==0: # In case we have gone too far
            if nip1==1: out=np.append(out,[i+n-2,j])
            if nim1==1: out=np.append(out,[i-n+2,j])
            if njp1==1: out=np.append(out,[i,j+n-2])
            if njm1==1: out=np.append(out,[i,j-n+2]) 
        n=n+1
        var=len(out)
         
    return(out) # closest coastal point
        

In [47]:
# def find_nearest_coast_point(i,j,mask,rnf_data,nseuil):
#     out=[]
#     n=1
#     var=0
#     nip1,nim1,njp1,njm1 = 0 ,0 ,0 ,0 
#     while (var==0) and (n<nseuil):
#         if mask[i+n,j]==1:
#             if (rnf_data[i+n-1,j] == 0.):
#                 out=np.append(out,[i+n-1,j])
#         if mask[i-n,j]==1:
#             if (rnf_data[i-n+1,j] == 0.):
#                 out=np.append(out,[i-n+1,j])
#         if mask[i,j+n]==1:
#             if (rnf_data[i,j+n-1] == 0.):
#                 out=np.append(out,[i,j+n-1])
#         if mask[i,j-n]==1:
#             if (rnf_data[i,j-n+1] == 0.):
#                 out=np.append(out,[i,j-n+1])  

#         n=n+1
#         var=len(out)
         
#     return(out) # closest coastal point
        

In [54]:
def move_runoffs(rnf_2D,rnf_point,mask,lverb):
# --------------------------------------------------------------------------------------------------
# PURPOSE :
# Check runoff data and move data off the coast or over land at the first available point near the coast
# ------------------------------------
# CASE 1 : Runoff point is over land : 
# find the nearest(s) sea point(s) and return its (their) index : ind=(i,j) or ind(i1,j1,i2,j2....)
# 2 possibilities : 
#    => At least one runoff value at ind=(in,jn) is 0.0 : move data over this point
#    => No runoff value at ind=(in,jn) is > 0.0 : add runoff value to this point
# When more than one sea point is found (ind(i1,j1,i2,j2....)), the runoff is averaged over every points
#
# ------------------------------------
# CASE 2 : Runoff point is surrounded by sea : 
# Find the nearest coast point
# If more than one coast points are available, average avor the two coast points
#
#
# --------------------------------------------------------------------------------------------------
# Inputs : 
# rnf_2D = runoff data in 2 dimension
# rnf_point = array with indexes of rnf points (should have the form : (2,N), 
# where N is the number of runoff points)
# mask = output mask (1 over sea points and 0 over land points)
# lverb = verbose (True or False)
# --------------------------------------------------------------------------------------------------
# Output : New 2D array with moved runoffs
# --------------------------------------------------------------------------------------------------

# Initialisation
    nseuil=30 # over 30 points distance, do not replace runoff
    rnf_2D_new = np.copy(rnf_2D)
    mask_data=mask
    mask_data=np.where(mask_data==1,0,1) # invert mask
    sea_point_not_found=0.
    ndist=1
    
# --------------------------------------------------------------------------------------------------
# BEGIN LOOP

# Loop over valid runoff values only  
    for n in range(len(rnf_point[0,:])): 
        N_earth_points_i, N_earth_points_j = check_mask_nearby(rnf_point[0,n],\
                                                               rnf_point[1,n],mask_data,ndist)
        N_earth_points_ij = N_earth_points_i + N_earth_points_j
        
# CASE 1 : POINT IS OVER LAND ------------
        if(N_earth_points_ij > 0): # at least one earth point nearby
            if (mask_data[rnf_point[0,n],rnf_point[1,n]]==1):
                if lverb: print("==> j, i = ", rnf_point[0,n],rnf_point[1,n],                    \
                                "is on mask point with", N_earth_points_i -1                     \
                      ,"earth points along i nearby and", N_earth_points_j - 1,                  \
                     "points along j")
                    
    # CASE 1.1 : POINT IS SURROUNDED BY EARTH ------------
            # Loop until we find at least one sea point in ndist perimeter
                if N_earth_points_ij == 6: # Surrounded by earth
                    if (ndist > nseuil): 
                        print("WARNING !!! : closest sea point is over ",nseuil,"\
                        point perimeter at i, j = ", rnf_point[0,n],rnf_point[1,n])

                    while sea_point_not_found == 0:
                        N_earth_points_i, N_earth_points_j =                                     \
                        check_mask_nearby(rnf_point[0,n],rnf_point[1,n],mask_data,ndist)
                        
                        N_earth_points_ij = N_earth_points_i + N_earth_points_j
                        
                        if N_earth_points_ij == ((1+ndist*2)*2): # No sea point in ndist perimeter 
                            if lverb: print(rnf_point[0,n],rnf_point[1,n],\
                                            "surrounded by earth points, trying ndist=+1;",      \
                                            N_earth_points_i, N_earth_points_j,(1+ndist*2)*2)
                            az=1
                        else: # At least one sea point in ndist perimeter
                            sea_point_not_found=1.                        
                            ind = find_nearest_sea_point(rnf_point[0,n],rnf_point[1,n],          \
                                                         mask_data,ndist,rnf_2D.values)
                            npoints = get_npoints(rnf_point[0,n],rnf_point[1,n],mask_data,       \
                                                  ndist,rnf_2D.values)
                        ndist=ndist+1
                        
                        
    # CASE 1.2 : AT LEAST ON SEA POINT in ndist=1 perimeter ------------
                else: # 
                    ind = find_nearest_sea_point(rnf_point[0,n],rnf_point[1,n],mask_data,        \
                                                 ndist,rnf_2D.values)
                    npoints = get_npoints(rnf_point[0,n],rnf_point[1,n],mask_data,ndist,         \
                                          rnf_2D.values)               
                # Now replace data
                if npoints == 0: 
                    # No available points nearby without an already existing runoff value => avoid
                    rnf_2D_new[rnf_point[0,n],rnf_point[1,n]] = 0.  
                    print(rnf_point[0,n],rnf_point[1,n],"ISSUE AT THIS POINT !!")
                if npoints == 1: 
                    rnf_2D_new[int(ind[0]),int(ind[1])] = rnf_2D_new[int(ind[0]),int(ind[1])]    \
                    + rnf_2D_new[rnf_point[0,n],rnf_point[1,n]]
                    rnf_2D_new[rnf_point[0,n],rnf_point[1,n]] = 0.   
                    if lverb: print("moving point j,i = ", rnf_point[0,n],rnf_point[1,n],        \
                                    "at point j,i = ", ind)
                if npoints == 2: 
                    rnf_2D_new[int(ind[0]),int(ind[1])] = rnf_2D_new[int(ind[0]),int(ind[1])]    \
                    + (rnf_2D_new[rnf_point[0,n],rnf_point[1,n]] / 2) 
                    rnf_2D_new[int(ind[2]),int(ind[3])] = rnf_2D_new[int(ind[2]),int(ind[3])]    \
                    + (rnf_2D_new[rnf_point[0,n],rnf_point[1,n]] / 2 )
                    rnf_2D_new[rnf_point[0,n],rnf_point[1,n]] = 0.
                    if lverb: print("dispatch point j,i = ", rnf_point[0,n],rnf_point[1,n],      \
                                    "at 2 points j1,i1,j2,i2 = ", ind)
                if npoints == 3: 
                    rnf_2D_new[int(ind[0]),int(ind[1])] = rnf_2D_new[int(ind[0]),int(ind[1])]     \
                    + (rnf_2D_new[rnf_point[0,n],rnf_point[1,n]] / 3 )
                    rnf_2D_new[int(ind[2]),int(ind[3])] = rnf_2D_new[int(ind[2]),int(ind[3])]     \
                    + (rnf_2D_new[rnf_point[0,n],rnf_point[1,n]] / 3) 
                    rnf_2D_new[int(ind[4]),int(ind[5])] = rnf_2D_new[int(ind[4]),int(ind[5])]     \
                    + (rnf_2D_new[rnf_point[0,n],rnf_point[1,n]] / 3) 
                    rnf_2D_new[rnf_point[0,n],rnf_point[1,n]] = 0.
                    if lverb: print("moving point j,i = ", rnf_point[0,n],rnf_point[1,n],         \
                                    "at 3 points j1,i1,j2,i2,j3,i3 = ", ind)

                                        
                if lverb: print("..........")

# CASE 2 : POINT IS SURROUNDED BY SEA ------------
        else: # no earth point nearby

            if lverb: print(rnf_point[0,n],rnf_point[1,n], "is in the middle of the sea",        \
                            N_earth_points_i, N_earth_points_j,mask_data[rnf_point[0,n]+1,rnf_point[1,n]])
            # ------------------------------------------------
            # Find nearest coast point from 1 to nseuil distance
            ind = find_nearest_coast_point(rnf_point[0,n],rnf_point[1,n],mask_data,rnf_2D.values,nseuil)
            npoints=len(ind)/2
            # ------------------------------------------------
                      
            if npoints == 0: # No available points nearby without an already existing runoff value => avoid
                rnf_2D_new[rnf_point[0,n],rnf_point[1,n]] = 0.  
                print("WARNING : point at i, j = ", rnf_point[0,n],rnf_point[1,n] ,              \
                      " is way too far from coast => ignore")
            if npoints == 1: 
                rnf_2D_new[int(ind[0]),int(ind[1])] = rnf_2D_new[int(ind[0]),int(ind[1])]        \
                + rnf_2D_new[rnf_point[0,n],rnf_point[1,n]]
                rnf_2D_new[rnf_point[0,n],rnf_point[1,n]] = 0.   
                if lverb: print("moving point j,i = ", rnf_point[0,n],rnf_point[1,n],            \
                                "at point j,i = ", ind)
            if npoints == 2: 
                rnf_2D_new[int(ind[0]),int(ind[1])] = rnf_2D_new[int(ind[0]),int(ind[1])]        \
                + (rnf_2D_new[rnf_point[0,n],rnf_point[1,n]] / 2) 
                rnf_2D_new[int(ind[2]),int(ind[3])] = rnf_2D_new[int(ind[2]),int(ind[3])]        \
                + (rnf_2D_new[rnf_point[0,n],rnf_point[1,n]] / 2 )
                rnf_2D_new[rnf_point[0,n],rnf_point[1,n]] = 0. 
                if lverb: print("dispatch point j,i = ", rnf_point[0,n],rnf_point[1,n],\
                                "at 2 points j1,i1,j2,i2 = ", ind)
            if npoints > 2: print(rnf_point[0,n],rnf_point[1,n],"OVER 2")
            if lverb: print("..........")

        sea_point_not_found=0.
        ndist=1
        # Next point
    return rnf_2D_new
# --------------------------------------------------------------------------------------------------
# END LOOP

In [49]:
year=2017

rnf_inp_file='/data/vdi/tbrivoal/PRE_PROCESSING_IMMERSE/RUNOFFS_eNEATL36/runoff_eNEATL36_BDY_y'+str(year)+'.nc'
inp_domain_cfg_file='/data/vdi/tbrivoal/PRE_PROCESSING_IMMERSE/RUNOFFS_eNEATL36/DOMAIN_CFG_FINALDOMAIN/domain_cfg_init.nc'
out_runoff_file='/data/vdi/tbrivoal/PRE_PROCESSING_IMMERSE/RUNOFFS_eNEATL36/runoff_eNEATL36_BDY2D_corrected_y'+str(year)+'.nc'
mask_file='/data/vdi/tbrivoal/PRE_PROCESSING_IMMERSE/RUNOFFS_eNEATL36/mesh_mask.nc'
output_folder="/data/vdi/tbrivoal/PRE_PROCESSING_IMMERSE/RUNOFFS_eNEATL36/"


In [50]:
# Open files
inp_rnf_2D=xr.open_dataset(rnf_inp_file)
inp_domain_cfg=xr.open_dataset(inp_domain_cfg_file,drop_variables={"x", "y",})
maskf=xr.open_dataset(mask_file,drop_variables={"x", "y",})


In [51]:
# Open variables
# mask_inp =  inp_domain_cfg.top_level.squeeze()
mask_inp =  inp_domain_cfg.top_level.squeeze()

# mask_inp = maskf.tmask[0,0,:,:].squeeze()
rnf_2D=inp_rnf_2D.runoffs_instant.squeeze()
rnf_2D_new=np.copy(rnf_2D)
print(rnf_2D.shape)
print(mask_inp.shape)

(365, 1894, 1294)
(1894, 1294)


In [55]:
rnf_point = np.array(np.where(rnf_2D[0,:,:].values>0)) # Assuming runoffs does not move
print(rnf_point.shape)
for i in range(len(rnf_2D[:,0,0])):
    print(i)
    rnf_2D_new[i,:,:]=move_runoffs(rnf_2D[i,:,:],rnf_point,mask_inp,False)

(2, 11139)
0
1455 928 OVER 2
1493 1012 OVER 2


1
1455 928 OVER 2
1493 1012 OVER 2


2
1455 928 OVER 2
1493 1012 OVER 2


3
1455 928 OVER 2
1493 1012 OVER 2


4
1455 928 OVER 2
1493 1012 OVER 2


...

1493 1012 OVER 2
361
1455 928 OVER 2


1493 1012 OVER 2
362


1455 928 OVER 2
1493 1012 OVER 2
363
1455 928 OVER 2


1493 1012 OVER 2
364
1455 928 OVER 2


1493 1012 OVER 2


In [53]:
year=2017 # year of runoff file

# Date variables ----------------------------------------------------------------------------------------
dstart_year= str(year) + "-01-01" # 1st day of the year
dend_year= str(year) + "-12-31" # last day of the year

dstart_clim_monthly = str(year) + "-01-15" # for 12 month clim
dend_clim_monthly = str(year) + "-12-15" # for 12 month clim
dstart_minus_1_month = str(year-1) + "-12-01" # used for conversion from monthly to daily clim data

############################ Save in a Netcdf ###################################
# time_counter_daily = pd.date_range(dstart_year,dend_year, freq="D") # time dimension

# time_counter_daily_float = pd.to_numeric(time_counter_daily, downcast='float')
#time_counter_daily.values.astype("float")
# Create xarray dataarray
rnf_2D_daily_new_da = xr.DataArray(
    data=rnf_2D_new,
    dims=["time_counter", "y", "x"],
    coords=rnf_2D.coords,
    attrs=rnf_2D.attrs,
    name=rnf_2D.name,
     )



# # Create dataset
# ds = xr.merge([rnf_2D_daily_new_da, inp_rnf_2D.nav_lat, inp_rnf_2D.nav_lon])
# ds.attrs=inp_rnf_2D.attrs
# # Save to netcdf
# # outfile =   out_domain_cfg_file
outfile = out_runoff_file

rnf_2D_daily_new_da.to_netcdf(outfile, mode="w")

In [ ]:
print(np.nansum(rnf_2D_new[:,:,:]) - np.nansum(inp_rnf_2D.orca_costal[:,:,:]))